# Seizure prediction
Try to setup code to sample data before a seizure occurs and see if i can't generalize to a class for later analysis

In [1]:
import sys, os
sys.path.append(os.path.realpath(".."))

import util_funcs
from importlib import reload
reload(util_funcs)
from copy import deepcopy as cp

import data_reader as read
import pandas as pd
import numpy as np
import pickle as pkl
import matplotlib.pyplot as plt
import pywt
import tsfresh.feature_extraction.feature_calculators as feats
import constants
import clinical_text_analysis as cta
reload(cta)
import tsfresh
import ensembleReader as er
from sklearn.metrics import roc_auc_score, accuracy_score, confusion_matrix, roc_curve, r2_score
from os import path

reload(read)
import wf_analysis.datasets as wfdata
import wf_analysis.filters as filt
reload(filt)
from addict import Dict
import time
import pickle as pkl
import pyedflib as edf

Using Theano backend.


## Look at seizure labels

In [2]:
reload(read)
train_slr = read.SeizureLabelReader(split="train", return_tse_data=True, n_process=20)
dev_test_slr = read.SeizureLabelReader(split="dev_test", return_tse_data=True, n_process=20)
train_slr.verbosity = 1000
dev_test_slr.verbosity = 1000

In [3]:
allTrainLabels = train_slr[:]
allDevTestLabels = dev_test_slr[:]

Starting 20 processes
retrieving: 0
retrieving: 1000
retrieving: 2000
retrieving: 3000
Starting 20 processes
retrieving: 0


In [5]:
read.parse_edf_token_path_structure((train_slr.sampleInfo[3176]).token_file_path)[1]

'00008628'

In [4]:
reload(er)
eds = er.EdfDatasetSegments()

Starting 20 processes
retrieving: 0
Starting 20 processes
retrieving: 0
retrieving: 1000
retrieving: 2000
retrieving: 3000


In [6]:
train_labels = eds.get_train_split()

In [ ]:
for i, j  in train_labels[0][1].iteritems():
    print(i, j)

## Worked on pulling data based on seizure label

In [14]:
reload(er)
edss = read.Flattener(read.EdfFFTDatasetTransformer(er.EdfDatasetSegmentedSampler(segment_file_tuples=train_labels, num_samples=3000, max_bckg_samps_per_file=1, n_process=16, mode=er.EdfDatasetSegmentedSampler.PREDICT_MODE), freq_bins=[0,3.5,7.5,14,20,25,40], is_pandas_data=False,), n_process=16)
edss.verbosity=1000

In [11]:
from imblearn.over_sampling import SMOTE
smote = SMOTE()

In [15]:
data = edss[:]
x = [datum[0] for datum in data]
y = [datum[1] for datum in data]
smote = SMOTE(n_jobs=12)

Starting 16 processes
retrieving: 0
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 reque

read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 reque

read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read

In [16]:
sum(y)/ len(y)

0.6836666666666666

In [12]:
x_res, y_res = smote.fit_resample(x, y)

In [13]:
sum(y_res) / len(y_res)

0.5

In [40]:
sum(y) / len(y)

0.8506666666666667

In [19]:
#get number of samples generated that make a bckg event
sum([edss.sampleInfo[i].label for i in range(len(edss))])

19753

In [20]:
len(edss)

117260

1462754

In [21]:
sum([train_labels[i][1].index.max()/pd.Timedelta(seconds=4) for i in range(len(train_labels))])

1470264.0

In [26]:
from time import time

In [27]:
start = time()
reload(read)
scratchData = read.Flattener(read.EdfFFTDatasetTransformer(edss, freq_bins=[0,3.5,7.5,14,20,25,40], is_pandas_data=False), n_process=20)
scratchData.verbosity=500
scratchData = scratchData[:]

Starting 20 processes
retrieving: 0
read 1000, less than 4005 requested!!!
read 1000, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 1000, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 1000, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 1000, less than 4005 requested!!!
read 1000, le

read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
r

read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!

read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 reque

read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 9 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read 0, less than 4005 requested!!!
read

...

read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
r

read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
r

read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
r

read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read

read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 9 requested!!!
read 0, less than 9 requested!!!
read 0, less than 9 requested!!!
read 0, less than 9 requested!!!
read 0, less than 9 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less than 1030 requested!!!
read 0, less 

In [28]:
print(time() - start)

802.7979028224945


## Trying out imblearn to see if resampling data to deal with data imbalance can help here

In [ ]:
from imblearn.over_sampling import SMOTE

In [5]:
containsSeizures = []
for i, label in enumerate(allTrainLabels):
    if not (label.label == "bckg").all():
        containsSeizures.append(i)

In [6]:
len(containsSeizures)

458

In [7]:
seizureSubsetFiles = [train_slr.sampleInfo[i].token_file_path for i in containsSeizures]

In [8]:
cooldown = 5
possibleSampleTime = 20
print(allTrainLabels[containsSeizures[0]])
possibleSeizureTrainTimes = []
possibleNonseizureTrainTimes = []

     start      end label  p duration
0        0  62.6836  bckg  1  62.6836
1  62.6836  100.449  fnsz  1  37.7656
2  100.449      601  bckg  1  500.551


In [9]:
raw_ann = allTrainLabels[containsSeizures[200]]
raw_ann

start      end label  p duration
0         0        1  bckg  1        1
1         1  125.372  fnsz  1  124.372
2   125.372  348.232  bckg  1   222.86
3   348.232    407.9  fnsz  1   59.668
4     407.9  766.256  bckg  1  358.356
5   766.256  982.256  fnsz  1      216
6   982.256  1062.27  bckg  1   80.016
7   1062.27  1234.17  fnsz  1  171.896
8   1234.17  1469.23  bckg  1   235.06
9   1469.23  1565.19  fnsz  1   95.964
10  1565.19     1998  bckg  1  432.808

In [26]:
reload(read)
reload(er)
new_ann = er.seizure_series_annotate_times(raw_ann)

In [21]:
new_ann.index[new_ann == "bckg"] / pd.Timedelta(seconds=1)

Float64Index([ 131.0,  132.0,  133.0,  134.0,  135.0,  136.0,  137.0,  138.0,
               139.0,  140.0,
              ...
              1988.0, 1989.0, 1990.0, 1991.0, 1992.0, 1993.0, 1994.0, 1995.0,
              1996.0, 1997.0],
             dtype='float64', length=1044)

# Seizure Medication Labels

In [2]:
all_token_fns = read.get_all_token_file_names("train", "01_tcp_ar")

In [48]:
reload(read)
reload(cta)
clinical_note = cta.get_all_clinical_notes(all_token_fns[0])
print(clinical_note)

History:	29 year old woman with seizure onset last month.
Medications:	Keppra
Sedation:
EEG Type:	Awake & asleep
Technique:	International 10-20 System; standard 21 electrodes with T1/T2 electrodes and EKG
electrodes, awake, drowsy, asleep, hyperventilation, photic
Description:
Waking background is characterized by a 25-40uV, 9.5Hz alpha rhythm, which attenuates
symmetrically with eye opening.  Symmetric 5-15uV, 18-25Hz activity is present, maximal over
bilateral frontal regions.  During drowsiness, the background slows to central theta activity, frontal
beta activity becomes more prominent, and the alpha rhythm attenuates and becomes intermittent.
During brief stage 2 sleep, the record slows further to moderate voltage 2-4Hz activity, and
symmetric sleep spindles and K complexes appear.
No focal slowing is present.  No epileptiform discharges are present.
Hyperventilation is performed for 240 seconds with good cooperation, and produces no effect.
Stepped photic stimulation from 1-21 fl

In [54]:
import re

splits = re.match(r'(\\n)*\w+[\s\w+]*:', clinical_note)


<function Match.groups(default=None)>

In [69]:
splits.groupa

'History:'

In [37]:
len(splits)

2

"b'history:29 year old woman with seizure onset last month.medications:kepprasedation:eeg type:awake & asleeptechnique:international 10-20 system; standard 21 electrodes with t1/t2 electrodes and ekgelectrodes, awake, drowsy, asleep, hyperventilation, photicdescription:waking background is characterized by a 25-40uv, 9.5hz alpha rhythm, which attenuatessymmetrically with eye opening.  symmetric 5-15uv, 18-25hz activity is present, maximal overbilateral frontal regions.  during drowsiness, the background slows to central theta activity, frontalbeta activity becomes more prominent, and the alpha rhythm attenuates and becomes intermittent.during brief stage 2 sleep, the record slows further to moderate voltage 2-4hz activity, andsymmetric sleep spindles and k complexes appear.no focal slowing is present.  no epileptiform discharges are present.hyperventilation is performed for 240 seconds with good cooperation, and produces no effect.stepped photic stimulation from 1-21 flashes per second

In [16]:
splits[0]

"b'history:\\t29 year old woman with seizure onset last month.\\n'b'medications:\\tkeppra\\n'b'sedation:\\n'b'eeg type:\\tawake & asleep\\n'b'technique:\\tinternational 10-20 system; standard 21 electrodes with t1/t2 electrodes and ekg\\n'b'electrodes, awake, drowsy, asleep, hyperventilation, photic\\n'b'description:\\n'b'waking background is characterized by a 25-40uv, 9.5hz alpha rhythm, which attenuates\\n'b'symmetrically with eye opening.  symmetric 5-15uv, 18-25hz activity is present, maximal over\\n'b'bilateral frontal regions.  during drowsiness, the background slows to central theta activity, frontal\\n'b'beta activity becomes more prominent, and the alpha rhythm attenuates and becomes intermittent.\\n'b'during brief stage 2 sleep, the record slows further to moderate voltage 2-4hz activity, and\\n'b'symmetric sleep spindles and k complexes appear.\\n'b'no focal slowing is present.  no epileptiform discharges are present.\\n'b'hyperventilation is performed for 240 seconds with 